# Debugging Python code 🐛💻🐍
Created by [Ryan Parker](https://github.com/rparkr).  
Aug 2023

This notebook is used to demonstrate different methods for debugging Python code. It covers live debugging, rather than logging for code monitoring and asynchronous debugging.

Each of the sections below has some code with a bug; we'll use different debugging techniques to find and fix the bugs.

## Types of errors
Python programmers encounter three types of errors: _syntax_ errors, _exceptions_, and _logic_ errors.

**Syntax errors**  
Syntax errors deal with code that cannot be understood by the Python interpreter: for example, referring to a packages that was not imported, not indenting a `for` block, or forgetting to put a colon after a function definition (`def` statement). Syntax errors can usually be identified ahead of time by a linter, otherwise, they are easy to identify based on the error message Python produces when the interpreter runs into code it does not understand. 

**Exceptions**  
Exceptions are syntactically correct Python code that cannot be executed due to an error during evaluation: for example, dividing by zero (`ZeroDivisionError`), trying to concatenate a string with an integer (`TypeError`), `ValueError`, `AssertionError`, and many others. Exceptions can be _handled_ or "caught" using `try ... except` statements. Uncaught exceptions will cause the code to "crash," halting the program and producing an error message and a traceback to help the programmer identify and resolve the error.

**Logic errors**  
Logic errors are the trickiest of all. These errors are correctly written Python that does not cause an exception, but which produce unexpected behavior. Here's a simple example:  
```python
>>> def add_two_nums(a: float, b: float) -> float:
...    """Add two numbers and return the result"""
...    result = 2 * a + b
...    return result

>>> add_two_nums(2, 3)  # Expected result: 5
7
```

In this case, the error was that `a` was multiplied by `2` before being added to `b`. Logic errors sometimes come from changes made to one part of the codebase that impact another part, or from typos or other oversights. Debugging tools are very valuable when trying to locate and resolve logic errors.

**More info**  
For a quick review of syntax errors and exceptions, see the [chapter the Python tutorial](https://docs.python.org/3/tutorial/errors.html) and a [helpful overview from RealPython](https://realpython.com/python-exceptions/).

# Simple debugging: [Python Tutor](https://pythontutor.com/)
When first learning Python, it can be helpful to watch code execute one line at a time, especially when trying to understand flow control or recursive function behavior. [Python Tutor](https://pythontutor.com/) is a free online resource that visualizes code execution, line by line, showing variable references, intermediate values, and final outputs. Python Tutor runs only pure-Python code and does not support imported packages, besides a selection of modules from [Python's standard library](https://docs.python.org/3/library/index.html). Furthermore, Python tutor works with only Python 3.6 (which was released in 2016).

<span style="color: firebrick; font-weight: bold;">Note:</span> in general, I recommend using an IDE like Visual Studio Code for line-by-line code execution and debugging since VS Code has more advanced debugging features than Python Tutor and does not share its limitations. But if you come across some code online and want to quickly check how it works, Python Tutor can be a helpful tool.

The function below has an error. Try to identify it by copying the code and pasting into [PythonTutor.com](https://pythontutor.com/python-debugger.html#mode=edit)'s code visualizer.

In [1]:
def fib_number(n: int) -> int:
    '''Calculate the `n`th Fibonacci number.
    
    The first two numbers of the sequence are (0, 1). The `n`th number
    is the sum of the previous two Fibonacci numbers. Thus, the second Fibonacci
    number is 0 + 1 = 1. The third is 1 + 1 = 2; and so on.

    Examples:
    ```python
    >>> fib_number(4)
    3
    >>> fib_number(10)
    55
    >>> fib_number(20)
    6765
    >>> fib_number(100)
    354224848179261915075
    ```
    '''
    if n < 3:  # FIXME: here's the error
        return n
    else:
        return fib_number(n - 1) + fib_number(n - 2)

In [2]:
assert fib_number(10) == 55, f"Uh oh. fib_number(10) should be 55, but the result is {fib_number(10)}"

AssertionError: Uh oh. fib_number(10) should be 55, but the result is 89

# More complex debugging: VS Code
Visual Studio Code performs linting to identify problems adead of time, offers line-by-line execution for quickly checking code flow, and has advanced debugging tools to track down and resolve errors.

## Example 1: complex code flow
The function in this example recursively searches a (nested) dictionary for keys that match a user's query. Depending on the arguments passed to the function and the complexity of the dictionary being searched, the code flow can be difficult to follow without the aid of line-by-line execution or a debugger. We'll explore the use of VS Code's debugging tools to track the function's progress to search for matching keys.

Background on the function:  
The core idea is searching for a term within a list (since `mydict.keys()` returns a list). Here’s [a helpful StackOverflow answer](https://stackoverflow.com/questions/3640359/regular-expressions-search-in-list/39593126#39593126) that shows how to do that.

The search function is handled by the `regex` package, which adds fuzzy matching functionality to Python’s basic `re` module. See this [blog post from Max Halford](https://maxhalford.github.io/blog/fuzzy-regex-matching-in-python/) for a brief explanation. More details are found in [the `regex` GitHub repo](https://github.com/mrabarnett/mrab-regex#approximate-fuzzy-matching-hg-issue-12-hg-issue-41-hg-issue-109).

In [ ]:
# %pip install regex

In [3]:
import regex
import numpy as np

def dict_search(
    search_term: str,
    search_dict: dict,
    fetch_all: bool=True,
    fuzzy_constraints: str='{s,i,2i+4s<=4}',
    search_dict_name: str=''):
    '''Search for a term within the keys of a (nested) dictionary.

    Parameters
    ----------
    search_term: str
        The term you want to find among the keys of a (potentially nested)
        dictionary.

    search_dict: dict
        The dictionary whose keys will be searched for a matching term. Leave
        this as the top-level dict variable, such as `my_dict`, not 
        `my_dict['subdict']`, since this function uses the top-level dict to
        trace down each level.

        If you want to search starting at a particular key (like 
        `my_dict['subdict']`), then use `my_dict['subdict']` for the
        search_dict parameter and specify the search_dict_name parameter
        as "my_dict['subdict']".

    fetch_all: bool, default=True
        If `True` (default), print all matching keys across all levels of
        the (nested) dictionary. If `False`, stop printing matches after the
        first level where a match is found.

    fuzzy_constraints: str, default='{s,i,2i+4s<=4}'
        Searches are based on "fuzzy matching" logic, where a matched dict key
        does not need to be an exact match. For example, a search for "price"
        would also return results for "pricing" or "prices".

        The constraints are:
        {substitutions, insertions, deletions, weighting_factor}.

        For example: {e<=3} will match any string where there are
        at most 3 differences ("errors") between the matched value and the
        searched term. {s<=3,i<=3,d<=3} will match any string where there are
        at most 3 substitutions (e.g., "run" has 1 substitution from "ran"),
        3 insertions (e.g., "strep" has 1 insertion from "step"), and
        3 deletions (e.g. "bach" has 1 deletion from "beach").

        The weighting factors enable you to set the cost of each kind of error,
        prioritizing some errors over others in the matching logic.
        For example, {s,i,d,2i+3d+4s<=5} allows substitutions, insertions,
        and deletions, where the cost of each insertion is 2, the cost of each
        deletion is 3, and the cost of each substition is 4, with the total
        cost limited to no more than 5, which allows 2 insertions, 1
        substitution, 1 deletion, or 1 insertion and 1 deletion together.

        For more info, see: https://github.com/mrabarnett/mrab-regex#approximate-fuzzy-matching-hg-issue-12-hg-issue-41-hg-issue-109

    search_dict_name: str, default=''
        The name of the dictionary variable that will be searched. If the
        search_dict parameter is a top-level dictionary (like `mydict`), this
        should be left at its default (the empty string ''). If the
        search_dict parameter is a sub-level in the dictionary (like
        `my_dict['subdict']`, then this should be a string of that variable
        name ("my_dict['subdict']").


    Returns
    -------
    `None`. Results are printed for each key that matches the search term.

    Notes
    -----
    Inspiration for this method came from the following two sources:
    - Searching through a list: https://stackoverflow.com/questions/3640359/regular-expressions-search-in-list/39593126#39593126
    - Fuzzy matching: https://maxhalford.github.io/blog/fuzzy-regex-matching-in-python/

    '''

    # Store the name of the dictionary being searched
    # Reference: https://bobbyhadz.com/blog/python-print-variable-name
    if search_dict_name == '':
        globals_dict = globals()
        search_dict_name = [var_name for var_name in globals_dict if (globals_dict[var_name] is search_dict)][0]
        del globals_dict

    # Perform the fuzzy-match search across dict keys
    pattern = f"({search_term})" + fuzzy_constraints # Default: "{s,i,2i+4s<=4}" 
    results_list = list(filter(
        lambda s: regex.search(pattern, s, regex.BESTMATCH),
        search_dict.keys())
    )

    if np.array(results_list):  # FIXME: here's the error
        for item in results_list:            
            print(f"{search_dict_name}['{item}']")
        if fetch_all:
            # Recurse through nested dictionary levels
            for k in search_dict.keys():
                if type(search_dict[k]) == dict:
                    dict_search(search_term,
                                search_dict[k], 
                                fetch_all=fetch_all, 
                                fuzzy_constraints=fuzzy_constraints, 
                                search_dict_name=f"{search_dict_name}['{k}']")
                # Also search through lists if there are lists-of-dicts
                elif type(search_dict[k]) == list:
                    for n, subitem in enumerate(search_dict[k]):
                        if type(subitem) == dict:
                            dict_search(search_term,
                                        subitem, 
                                        fetch_all=fetch_all, 
                                        fuzzy_constraints=fuzzy_constraints, 
                                        search_dict_name=f"{search_dict_name}['{k}'][{n}]")

    else:
        # Recurse through nested dictionary levels
        for k in search_dict.keys():
            if type(search_dict[k]) == dict:
                dict_search(search_term,
                            search_dict[k], 
                            fetch_all=fetch_all, 
                            fuzzy_constraints=fuzzy_constraints, 
                            search_dict_name=f"{search_dict_name}['{k}']")
            # Also search through lists if there are lists-of-dicts
            elif type(search_dict[k]) == list:
                    for n, subitem in enumerate(search_dict[k]):
                        if type(subitem) == dict:
                            dict_search(search_term,
                                        subitem, 
                                        fetch_all=fetch_all, 
                                        fuzzy_constraints=fuzzy_constraints, 
                                        search_dict_name=f"{search_dict_name}['{k}'][{n}]")

Test the function using weather forecast data for Frisco, TX, from [Open-Meteo.com](https://open-meteo.com/en/docs), an open-source API for weather forecasts and weather history.

In [ ]:
# %pip install --upgrade requests

In [4]:
import json         # convert JSON to Python dictionaries and vice-versa
import requests     # make API calls (and other web requests)

r = requests.get(url=(
    'https://api.open-meteo.com/v1/forecast?'
    'latitude=33.1507'
    '&longitude=-96.8236'
    '&hourly='
        'temperature_2m,'
        'relativehumidity_2m,'
        'apparent_temperature,'
        'precipitation_probability,'
        'precipitation,'
        'weathercode,'
        'surface_pressure,'
        'cloudcover,'
        'visibility,'
        'windspeed_10m,'
        'winddirection_10m,'
        'temperature_180m,'
        'uv_index,'
        'is_day'
    '&current_weather=true'
    '&timezone=America%2FChicago'
    # '&past_days=3'
    '&forecast_days=7'))

forecast = r.json()

In [16]:
# Search for a weather variable
dict_search('temp', forecast, search_dict_name='forecast')

# Expected output:
# ````````````````
# forecast['current_weather']['temperature']
# forecast['hourly_units']['temperature_2m']
# forecast['hourly_units']['apparent_temperature']
# forecast['hourly_units']['temperature_180m']
# forecast['hourly']['temperature_2m']
# forecast['hourly']['apparent_temperature']
# forecast['hourly']['temperature_180m']

forecast['current_weather']['temperature']
forecast['hourly_units']['temperature_2m']
forecast['hourly_units']['apparent_temperature']
forecast['hourly_units']['temperature_180m']
forecast['hourly']['temperature_2m']
forecast['hourly']['apparent_temperature']
forecast['hourly']['temperature_180m']


## Example 2: PyTorch
Aligning tensor dimensions for opertations in neural networks can be tricky. Packages like [`tensor-sensor`](https://github.com/parrt/tensor-sensor) can help with visualizing the tensor operations, but debugging tools can also be very valuable, especially variable introspection during execution. We'll explore how to use that feature in this section.

The code in this section trains a neural network to use embeddings from text to output a score (such as a rating given a review text or a likelihood of default given a description of past credit activity).



Import packages

In [ ]:
# %pip install --upgrade pandas
# %pip install --upgrade torch
# %pip install --upgrade sentence-transformers

Load a dataset with text and a numerical target. This example uses Amazon review and star ratings, but you could substitute it for any dataset that has text and a numerical target.

In [45]:
import pandas as pd

data_dict = []  # store the results

# Download a dataset with text and corresponding numeric scores
# I learned about this data source from: https://huggingface.co/learn/nlp-course/chapter7/5?fw=pt
for batch_num in range(10):
    # Total dataset size is 200,000
    offset = (200_000 // 10) * batch_num
    r = requests.get(url=(
        'https://datasets-server.huggingface.co/rows'
        '?dataset=amazon_reviews_multi'
        '&config=en'
        '&split=train'
        f"&offset={offset:.0f}"
        '&limit=100'  # only 100 records can be retrieved at a time using this API endpoint
        ))

    for row in r.json()['rows']:
        data_dict.append(row['row'])

df = pd.DataFrame.from_dict(data_dict)
print(f"Dataframe shape: {df.shape}")
df.sample(5)

Dataframe shape: (1000, 8)


review_id          product_id          reviewer_id  stars  \
440  en_0409535  product_en_0107151  reviewer_en_0537364      3   
332  en_0075763  product_en_0455458  reviewer_en_0190657      2   
105  en_0402064  product_en_0705879  reviewer_en_0367583      1   
721  en_0373372  product_en_0695355  reviewer_en_0716082      4   
81   en_0754503  product_en_0033757  reviewer_en_0698198      1   

                                           review_body  \
440  I’ve had other mattress pads that are waterpro...   
332  Just watch out that you do get all (4) boxes t...   
105  Ordered this for a Christmas gift for my grand...   
721  So easy. Just pull it out of the box and paint...   
81               Don’t purchase. They have no cushion.   

                                          review_title language  \
440    and this one feels like plastic. Not a huge fan       en   
332                                   Only got (1) box       en   
105  Don’t order from here if you don’t want to dis...       en   
721                                          Great buy       en   
81                                    Horrible quality       en   

    product_category  
440             home  
332          grocery  
105              toy  
721             home  
81             other

Create embeddings of the sentences to be used in our neural network. See the [sentence-transformers](https://github.com/UKPLab/sentence-transformers) GitHub repo for more information on creating the sentence embeddings.

Normally, embedding information would be extracted in the `Dataset` class, but for this debugging training, we'll pre-embed the dataset and save it.

In [46]:
from sentence_transformers import SentenceTransformer
model = SentenceTransformer('all-MiniLM-L6-v2')

# Load the sentences in a NumPy array
sentences = df.review_body.values

# Embed the sentences
embeddings = model.encode(sentences)

print(type(embeddings))
print(embeddings.shape)  # 1000 sentences; embedding space of 384 dimensions

<class 'numpy.ndarray'>
(1000, 384)


This function saves the embeddings as a .csv file formatted as an HTML link, which is saved with the notebook. This is used to facilitate the debugging training, so learners don't need to install the `sentence-transformers` library.

In [47]:
import base64
from IPython.display import display, HTML

def download_link(
        data: pd.DataFrame | pd.Series | np.ndarray,
        filename: str = 'data',
        return_link: bool = False) -> str:
    """Generate an HTML-encoded string to download data."""
    if type(data) not in (pd.DataFrame, pd.Series):
        data = pd.DataFrame(data)
    # Technique adapted from: https://discuss.streamlit.io/t/heres-a-download-function-that-works-for-dataframes-and-txt/4052
    csv = data.to_csv(index=False, header=False)
    b64 = base64.b64encode(csv.encode()).decode()
    href = f'<a href="data:file/csv;base64,{b64}" download="{filename}.csv">Download: {filename}.csv</a>'
    # Display the link
    display(HTML(href))
    if return_link:
        return href
    else:
        return None

download_link(data=embeddings, filename='embeddings')

In [48]:
download_link(data=df.stars, filename='stars')

After saving the data in the same folder as this notebook, load the data as NumPy arrays:

In [ ]:
embeddings = np.loadtxt('embeddings.csv')
stars = numpy.loadtxt('stars.csv')

# Or, if the DataFrame is still in memory:
# stars = df.stars.values

Set up Dataset and DataLoader for processing the data

In [93]:
import torch
import torch.nn as nn

batch_size = 32
train_pct = 0.7

# Create train/test split
rng = np.random.default_rng()
num_samples = stars.shape[0]
idxs = np.arange(1000)
rng.shuffle(idxs)  # shuffle indexes, in place
train_idxs = idxs[:np.ceil(num_samples * train_pct).astype(int)]
test_idxs = idxs[np.ceil(num_samples * train_pct).astype(int):]

class EmbeddingsDataset(torch.utils.data.Dataset):
    def __init__(self, train, data, labels, pre_embedded: bool = True, embedding_model = None):
        self.pre_embedded = pre_embedded
        self.embedding_model = embedding_model
        self.train = train
        if self.train:
            self.data = data[train_idxs]
            self.labels = data[train_idxs]  # FIXME: Here's the error
        else:
            self.data = data[test_idxs]
            self.labels = labels[test_idxs]

    def __len__(self):
        return len(self.data)

    def __getitem__(self, index):
        y = torch.tensor(self.labels[index]) - 1  # set to range [0, 4] to match argmax()
        if self.pre_embedded:
            return torch.tensor(self.data[index]), y
        else:
            embedding = torch.tensor(self.embedding_model.encode(self.data[index]))
            return embedding, y

train_dataset = EmbeddingsDataset(train=True, data=embeddings, labels=stars, pre_embedded=True)
test_dataset = EmbeddingsDataset(train=False, data=embeddings, labels=stars, pre_embedded=True)

train_dataloader = torch.utils.data.DataLoader(train_dataset, batch_size=batch_size, shuffle=True)
test_dataloader = torch.utils.data.DataLoader(test_dataset, batch_size=batch_size, shuffle=True)

Define the network architecture

In [121]:
class SmallNet(nn.Module):
    def __init__(self):
        super().__init__()  # inherit from nn.Module
        self.linear_layers = nn.Sequential(
            nn.Linear(384, 512),
            nn.ReLU(),  # non-linear activation function
            nn.Linear(512, 512),
            nn.ReLU(),
            nn.Linear(512, 5)  # 5 possible classes (stars 1-5); set to 1 to use as a regression task
        )
    
    def forward(self, x):
        return self.linear_layers(x)

device = "cuda" if torch.cuda.is_available() else "cpu"

net = SmallNet().to(device)

total_params = 0
for layer in net.parameters():
    total_params += layer.numel()

print(f"This network has {total_params:,.0f} parameters.\nHere's its architecture:")

print(net)

This network has 462,341 parameters.
Here's its architecture:
SmallNet(
  (linear_layers): Sequential(
    (0): Linear(in_features=384, out_features=512, bias=True)
    (1): ReLU()
    (2): Linear(in_features=512, out_features=512, bias=True)
    (3): ReLU()
    (4): Linear(in_features=512, out_features=5, bias=True)
  )
)


Train the model

See: [PyTorch Quickstart for a walkthrough of this code](https://pytorch.org/tutorials/beginner/basics/quickstart_tutorial.html)

In [122]:
learning_rate = 1e-4

loss_fn = nn.CrossEntropyLoss()  # or nn.MSELoss() for regression tasks
optimizer = torch.optim.Adam(net.parameters(), lr=learning_rate)

def train_loop(dataloader, model, loss_fn, optimizer):
    size = len(dataloader.dataset)
    model.train()  # set model in training mode for batch norm and dropout (not implemented in this network)
    for batch, (X, y) in enumerate(dataloader):
        # Compute prediction and loss
        pred = model(X)
        loss = loss_fn(pred, y)

        # Backpropagation
        loss.backward()
        optimizer.step()
        optimizer.zero_grad()

        if batch % 10 == 0:
            loss, sample_num = loss.item(), (batch + 1) * len(X)
            print(f"loss: {loss:>7f}  [{sample_num:d}/{size:d}]")


def test_loop(dataloader, model, loss_fn):
    model.eval()  # in eval mode, batch norm and dropout are turned off
    size = len(dataloader.dataset)
    num_batches = len(dataloader)
    test_loss, correct = 0, 0
    with torch.no_grad():  # don't track gradients in testing mode
        for X, y in dataloader:
            pred = model(X)
            test_loss += loss_fn(pred, y).item()
            correct += (pred.argmax(1) == y).type(torch.float).sum().item()

    test_loss /= num_batches
    correct /= size
    print(f"Test Error:\nAccuracy: {(100*correct):>0.1f}%, Avg loss: {test_loss:>8f}\n")

In [123]:
epochs = 10
for e in range(epochs):
    print(f" Epoch {e+1} ".center(50, '='))
    train_loop(train_dataloader, net, loss_fn, optimizer)
    test_loop(test_dataloader, net, loss_fn)
print(' DONE '.center(50, '='))

==================== Epoch 1 =====================
loss: 1.609187  [32/700]
loss: 1.614176  [352/700]
loss: 1.607091  [672/700]
Test Error:
Accuracy: 19.0%, Avg loss: 1.609124

==================== Epoch 2 =====================
loss: 1.605719  [32/700]
loss: 1.601681  [352/700]
loss: 1.610297  [672/700]
Test Error:
Accuracy: 22.3%, Avg loss: 1.606007

==================== Epoch 3 =====================
loss: 1.600988  [32/700]
loss: 1.599045  [352/700]
loss: 1.590527  [672/700]
Test Error:
Accuracy: 27.3%, Avg loss: 1.600357

==================== Epoch 4 =====================
loss: 1.597991  [32/700]
loss: 1.582960  [352/700]
loss: 1.583435  [672/700]
Test Error:
Accuracy: 29.0%, Avg loss: 1.591195

==================== Epoch 5 =====================
loss: 1.583639  [32/700]
loss: 1.569664  [352/700]
loss: 1.559601  [672/700]
Test Error:
Accuracy: 32.0%, Avg loss: 1.576993

==================== Epoch 6 =====================
loss: 1.550275  [32/700]
loss: 1.520950  [352/700]
loss: 1.54591

# Python's built-in `pdb` module
Even if you don't have access to powerful debugging tools from an IDE like VS Code, you can always use Python's built-in [`pdb` module](https://docs.python.org/3/library/pdb.html), for "Python DeBugger."

To use `pdb` in Python 3.7+, simply type `breakpoint()` on the line where you want to pause code execution and enter the `pdb` interactive Python prompt (REPL, or Read Execute Print Loop), which will enable you to inspect variables and run other commands. To resume code execution, run the command `continue`.

To use `pdb` in Python versions before 3.7, do the following:
```python
import pdb
...
<YOUR CODE HERE>
...
pdb.set_trace()
```

and the Python debugger interactive prompt will launch when the `pdb.set_trace()` statement is executed.

Once you've entered the Python debugger, [use these commands](https://docs.python.org/3/library/pdb.html#debugger-commands) along with any of your own Python code to inspect variables and move around the code.

In [28]:
import pdb

from bokeh.io import output_notebook
from bokeh.models import ColumnDataSource, HoverTool
from bokeh.plotting import figure, show
import pandas as pd

output_notebook()

Loading BokehJS ...

In [44]:
# Get weather forecast data
df = pd.read_csv(
    'https://api.open-meteo.com/v1/forecast?'
    'latitude=33.2362'
    '&longitude=-96.8011'
    '&hourly=temperature_2m,'
    'apparent_temperature'
    '&format=csv', skiprows=2, parse_dates=True)

pdb.set_trace()
# or, ...
# breakpoint()  # doesn't work in VS Code, Python 3.11.3

# Convert to datetime for proper representation in the plot
df.time = df.time.astype('datetime64[ns]')

source = ColumnDataSource(data=df)

# Plot data
p = figure(
        title='Temperature forecast for Prosper, TX',
        x_axis_label='Date', y_axis_label='Temperature (°C)',
        x_axis_type='datetime')

p.line(x='time', y='temperature_2m (°C)', legend_label='temp',
       color='firebrick', source=source)
p.line(x='time', y='apparent_temperature (°C)', legend_label='apparent temp',
       source=source)

hover = HoverTool()
hover.tooltips = [
    ('time', '@time{%Y-%m-%d %H:%M}'),
    ('temp °C', '@{temperature_2m (°C)}{0.0}'),
    ('feels like', '@{apparent_temperature (°C)}{0.0}')
]

hover.formatters = {'@time': 'datetime'}

p.add_tools(hover)

show(p)